In [49]:
import plotly.graph_objects as go

In [50]:
def gorizont_coord(file):
   with open(file, 'r') as f:
       gorizon = []
       for line in f:
           if not line.startswith('#'):  # Пропуск строк, начинающихся с #
               x, y, z, *rest = line.split()  # Разбиение строки по столбцам
               x = int(x.split('.')[0])  # Получение целочисленного значения из первого столбца
               y = int(y.split('.')[0])  # Получение целочисленного значения из второго столбца
               z = int(z.split('.')[0])  # Получение целочисленного значения из третьего столбца
               gorizon.append([x, y, z])  # Добавление данных в словарь
          
   return gorizon

In [66]:
def proverka(top, bottom):
    otr_value = []
    map_otr = []
    for i in range(len(top)):
        map_otr.append([top[i][0], top[i][1], top[i][2] - bottom[i][2]])
        if top[i][2] - bottom[i][2] < 0:
            otr_value.append([top[i][0], top[i][1], top[i][2] - bottom[i][2]])
    return otr_value, map_otr

In [67]:
def plot_map_2(data, red_points):
    # Извлечение данных для отрисовки
    x_coords = [point[0] for point in data]
    y_coords = [point[1] for point in data]
    z_values = [point[2] for point in data]

    # Извлечение координат красных точек
    red_x_coords = [point[0] for point in red_points]
    red_y_coords = [point[1] for point in red_points]

    # Создание графика
    fig = go.Figure(data=[
        go.Scatter(x=x_coords, y=y_coords, mode='markers', marker=dict(color=z_values, colorscale='Viridis', showscale=True, colorbar_title='Значения')),
        go.Scatter(x=red_x_coords, y=red_y_coords, mode='markers', marker=dict(color='red', size=5))
    ])

    # Настройка графика
    fig.update_layout(
        title='Карта толщин',
        width=800,
        height=600,
        margin=dict(l=50, r=50, t=50, b=50)
    )

    # Отображение графика
    fig.show()



In [68]:
def plot_otr_values(points, coord, value):
    # Фильтрация точек по координате
    filtered_points = [point for point in points if point[coord] == value]

    # Извлечение значений и координат
    values = [point[2] for point in filtered_points]
    coords = [point[1 - coord] for point in filtered_points]

    # Построение графика
    fig = go.Figure(data=[go.Scatter(x=coords, y=values)])
    fig.update_layout(title=f"График значений при {['Инлайн', 'Икслаин'][coord]} = {value}",
                      xaxis_title=['Инлайн', 'Икслаин'][1 - coord],
                      yaxis_title='Значение')

    # Вывод графика
    fig.show()


In [69]:
def group_points(points):
    # Создание словарей для группировки точек по прямым
    x_lines = {}
    y_lines = {}

    # Группировка точек по прямым
    for point in points:
        if len(point) > 0:
            x = point[0]
            y = point[1]

            # Группировка по прямым, параллельным оси X
            if x not in x_lines:
                x_lines[x] = []
            x_lines[x].append(point)

            # Группировка по прямым, параллельным оси Y
            if y not in y_lines:
                y_lines[y] = []
            y_lines[y].append(point)

    # Объединение групп точек по прямым
    lines = list(x_lines.values()) + list(y_lines.values())

    # Исключение прямых, содержащих только одну точку
    lines = [line for line in lines if len(line) > 1]

    return lines



In [70]:
Top_TWT = gorizont_coord('C:/HV/Seismic/datas/TWT_Top_U1.txt')
Bottom_TWT = gorizont_coord('C:/HV/Seismic/datas/TWT_Bottom_U1_otr.txt')
otr_value_TWT, otr_map_TWT = proverka(Top_TWT, Bottom_TWT)
if len(otr_value_TWT) != 0:
    print(f"Нижележащая поверхность подошвы оказалась выше вышележащей поверхности кровли (несоответствие на {round(len(otr_value_TWT)*100 / len(otr_map_TWT), 3)}% площади). Проверьте корректность пикировки сейсмических данных")
    plot_map_2(otr_map_TWT, otr_value_TWT)
    lines = group_points(otr_value_TWT)
    inline_otr = []
    xline_otr = []
    for i in range(len(lines)):
        if lines[i][0][0] - lines[i][1][0] == 0:
            inline_otr.append(lines[i][0][0])
        elif lines[i][0][1] - lines[i][1][1] == 0:
            xline_otr.append((lines[i][0][1]))
    if len(inline_otr) != 0:
        for i in range(len(inline_otr)):   
            plot_otr_values(otr_map_TWT, 0, inline_otr[i]) # 0 - Inline , 1 - Xline

    if len(xline_otr) != 0:
        for i in range(len(xline_otr)):   
            plot_otr_values(otr_map_TWT, 1, xline_otr[i]) # 0 - Inline , 1 - Xline
else:
    print('Данные корректны')


Нижележащая поверхность подошвы оказалась выше вышележащей поверхности кровли (несоответствие на 0.054% площади). Проверьте корректность пикировки сейсмических данных


In [74]:
Top_TVDSS = gorizont_coord('C:/HV/Seismic/datas/TVDSS_Top_U1.txt')
Bottom_TVDSS = gorizont_coord('C:/HV/Seismic/datas/TVDSS_Bottom_U1.txt')
otr_value_TVDSS, otr_map_TVDSS = proverka(Top_TVDSS, Bottom_TVDSS)
if len(otr_value_TVDSS) != 0:
    print(f"Нижележащая структурная карта подошвы оказалась выше вышележащей структурной карты кровли (несоответствие на {round(len(otr_value_TVDSS)*100 / len(otr_map_TVDSS), 3)}% площади). Проверьте корректность пикировки сейсмических данных и корректность скоростной модели. Вероятно, была произведена подсадка скважин на отбивки и возникло перекрытие структурных карт")
    plot_map_2(otr_map_TVDSS, otr_value_TVDSS)
    lines = group_points(otr_value_TVDSS)
    inline_otr = []
    xline_otr = []
    for i in range(len(lines)):
        if lines[i][0][0] - lines[i][1][0] == 0:
            inline_otr.append(lines[i][0][0])
        elif lines[i][0][1] - lines[i][1][1] == 0:
            xline_otr.append((lines[i][0][1]))
    if len(inline_otr) != 0:
        for i in range(len(inline_otr)):   
            plot_otr_values(otr_map_TVDSS, 0, inline_otr[i]) # 0 - Inline , 1 - Xline

    if len(xline_otr) != 0:
        for i in range(len(xline_otr)):   
            plot_otr_values(otr_map_TVDSS, 1, xline_otr[i]) # 0 - Inline , 1 - Xline
else:
    print('Данные корректны')

Данные корректны
